In [350]:
# load portfolio
db_url = 'sqlite:///local.db'
from backgroundTask import update_portfolio_profile_to_db
from sqlalchemy import create_engine
import pandas as pd
from script import api
from script.utils import time_in_beijing
from bokeh.models.widgets.tables import CheckboxEditor, NumberEditor, SelectEditor
import io
import pytz
import datetime as dt
from script.utils import create_stocks_entry_from_excel, style_number, create_share_changes_report
import panel as pn
pn.extension()
pn.extension('tabulator')
pn.extension('plotly')
pn.extension('floatpanel')



In [351]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [352]:
# the width of iphone se
MIN_COMPONENT_WIDTH = 375
MAX_COMPONENT_WIDTH = 600

In [353]:
## create df for portfolio profile ui
with create_engine(db_url).connect() as conn:
    p_profile = pd.read_sql_table('portfolio_profile', con=conn)
    p_profile.date = pd.to_datetime(p_profile.date)
    stock_details = pd.read_sql_table('stocks_details', con=conn)
    # drop index for visual
    # p_profile = p_profile.drop(columns=['index'])
    
    # calculate change in shares
    p_profile.sort_values(by=['date'], inplace=True)
    # change in shares for same ticker
    p_profile['share_changes'] = p_profile.groupby(['ticker'])['shares'].diff()
    # if change is null fill with shares
    p_profile['share_changes'] = p_profile['share_changes'].fillna(p_profile['shares'])
    # indicate if change is saved
    p_profile['change_saved'] = True
    p_profile['sync_to_db'] = True

# all stock option for auto fill
all_tickers = stock_details.ticker.to_list()

# get most recent portfolio 
most_recent_portfolio = p_profile[p_profile.date == max(p_profile.date)]

In [354]:
## create portfolio table tabulator

hidden_column = ['index','sector','name']
col_to_titles = {'ticker':'证劵代码', 'weight':'初始现金',
                 'date':'时间','aggregate_sector':'股票分类',
                 'display_name':'股票名称',
                 'shares':'持仓','change_saved':'已同步到数据库',
                 'sync_to_db':'存入数据库','share_changes':'持仓变化'
                 }
groupby=['date']
# editor
bokeh_editors = {
    'ticker': SelectEditor(options=all_tickers),
    'shares': NumberEditor(),
}
# require format，
tabulator_formatters = {
    # 'float': {'type': 'progress', 'max': 10},
    'sync_to_db': {'type': 'tickCross'},
    'change_saved': {'type': 'tickCross'},
}
# frozen_columns = ['date','ticker','display_name','shares','sync_to_db','change_saved']

portfolio_tabulator = pn.widgets.Tabulator(p_profile,layout='fit_columns', 
                                       width=1000, groupby=groupby,
                                       hidden_columns=hidden_column,titles=col_to_titles,
                                       formatters=tabulator_formatters,
                                       editors=bokeh_editors,
                                       pagination='remote',
                                       page_size=25,
                                       height_policy='max',
                                       sizing_mode='stretch_width',
                                    #    frozen_columns=frozen_columns
                                       )
portfolio_tabulator.style.apply(style_number,subset=['share_changes'])


print()


In [355]:
## create component

history_dt = p_profile[['date','sync_to_db']].copy()
# drop row with duplicate date
history_dt.drop_duplicates(subset='date', keep='first', inplace=True)

history_tabulator = pn.widgets.Tabulator(history_dt,
                                         formatters=tabulator_formatters, 
                                         buttons={'detail': "<i>📋</i>"},
                                         hidden_columns=hidden_column,
                                         height_policy='max',
                                         titles=col_to_titles)
new_stock_btn = pn.widgets.Button(name='增加新股票', button_type='primary', sizing_mode='stretch_width')
preview_btn = pn.widgets.Button(name='预览', button_type='primary',sizing_mode='stretch_width')
file_input = pn.widgets.FileInput(accept='.xlsx', sizing_mode='stretch_width')
# strip timezone info
datetime_picker = pn.widgets.DatetimePicker(name='Datetime Picker', 
                                            value=time_in_beijing().replace(tzinfo=None), 
                                            sizing_mode='stretch_width')
upload_to_db_btn = pn.widgets.Button(name='保存到数据库', button_type='warning',sizing_mode='stretch_width')
# emtpy stock_column to display new entires 
stock_column = pn.Column(width_policy='max',height_policy='max',scroll=True)
# floating window row
floating_windows = pn.Row()





In [356]:
## define event handler
def save_profile_changes(profile_df):
    '''
    handle save to db
    '''
    pass

def delete_stock(row):
    '''delete a stock entry'''
    stock_column.remove(row)

def create_new_stock_entry(ticker=None, shares=None, disable_ticker=True):
    '''create a new new stock entry'''
    delete_btn = pn.widgets.Button(name='❌', width=50, sizing_mode='fixed')
    text_input = pn.widgets.AutocompleteInput(value=ticker, restrict=False, disabled=disable_ticker,  sizing_mode='stretch_width') \
        if ticker else pn.widgets.AutocompleteInput(
            sizing_mode='stretch_width',
            options=all_tickers,
            placeholder='input ticker',
            
        )
    int_input = pn.widgets.IntInput(value=shares, step=1, start=0, sizing_mode='stretch_width') \
        if shares else pn.widgets.IntInput(placeholder='#shares', step=1, sizing_mode='stretch_width')
    
    row = pn.Row(
        delete_btn,
        text_input,
        int_input,
        width_policy='max',
    )
    delete_btn.on_click(lambda _, row=row: delete_stock(row))
    return row

def update_stock_column(xlsx_file=None):
    stock_entries = []
    if xlsx_file is None:
        for ticker, shares in most_recent_portfolio[['ticker','shares']].values:
            stock_entries.append(create_new_stock_entry(ticker=ticker, shares=shares))
    # create from xlsx_file
    else:
        stocks_list = create_stocks_entry_from_excel(xlsx_file)
        for entry in stocks_list:
            stock_entries.append(create_new_stock_entry(ticker=entry['ticker'], shares=entry['shares']))
        # modify time 
        datetime_picker.value = stocks_list[0]['date']
        file_input.value = None
        
    # update 
    stock_column.clear()
    stock_column.extend(stock_entries)

def update_profile_tabulator(e):
    '''add all stocks entry to ui'''
    new_entry = [dict(ticker=row[1].value,shares=row[2].value, date=datetime_picker.value) for row in stock_column]
    new_profile, error = api.update_portfolio_profile(new_entry)
    # calculate share changes
    tmp_profile = pd.concat([p_profile, new_profile], ignore_index=True)
    tmp_profile.sort_values(by='date', inplace=True)
    tmp_profile['share_changes'] = tmp_profile.groupby('ticker')['shares'].diff()
    tmp_profile['share_changes'] = tmp_profile['share_changes'].fillna(tmp_profile['shares'])
    new_profile = new_profile.merge(tmp_profile[['ticker','date','share_changes','change_saved']], on=['ticker','date'], how='left')
    # fill emtpy change_saved to False
    new_profile['change_saved'] = new_profile['change_saved'].fillna(False)
    new_profile['sync_to_db'] = True
    # update profile tabulator
    portfolio_tabulator.stream(new_profile)

def add_new_stock(e):
    row = create_new_stock_entry()
    stock_column.append(row)

def handle_click_on_history_tabulator(e):
    '''handle click click on history tabulator'''
    if e.column == 'detail':
        row_index = e.row
        date = history_tabulator.value.iloc[row_index]['date']
        date_str = date.strftime("%Y-%m-%d : %H:%M:%S")
        record_df = p_profile[p_profile.date == date]
        floatpanel = pn.layout.FloatPanel(create_share_changes_report(record_df), name=date_str, margin=20,position='right-top' ) 
        floating_windows.append(floatpanel)
def handle_sync_to_db(e):
    '''sync selected entry to db'''
    new_portfolio = portfolio_tabulator.value
    # only update selected row to db
    selected_portfolio = new_portfolio[new_portfolio['sync_to_db'] == True]
    update_portfolio_profile_to_db(selected_portfolio)
    # mark selected row as saved 
    selected_portfolio['change_saved'] = True
   


In [357]:
## register event handler 
upload_to_db_btn.on_click(handle_sync_to_db)
preview_btn.on_click(update_profile_tabulator)    
new_stock_btn.on_click(add_new_stock)
history_tabulator.on_click(
    handle_click_on_history_tabulator
)

In [358]:
## create handler component to add to panel so can be listened to
upload_xlsx_handler = pn.bind(update_stock_column,file_input)

In [359]:
## layout

editor_widget = pn.Column(floating_windows,datetime_picker, upload_to_db_btn, new_stock_btn, preview_btn, file_input, stock_column
                             ,width=MIN_COMPONENT_WIDTH, height_policy='max')
# app
app = pn.Row(
    pn.layout.HSpacer(),
    editor_widget,
    pn.Spacer(width=10),
    history_tabulator,
    pn.Spacer(width=10),
    portfolio_tabulator, 
    pn.Spacer(width=10),
    upload_xlsx_handler, 
    pn.layout.HSpacer(),
    width_policy='max', height_policy='max')
app.servable()

BokehModel(combine_events=True, render_bundle={'docs_json': {'cfb25722-80b1-49fe-917d-cc0c20ef53ac': {'version…